# Binary classification with the crabs data

The package is designed to handle models of the following general form
\begin{eqnarray}
\mathbf{y} \ |\ \mathbf{f}, \theta &\sim& \prod_{i=1}^n p(y_i \ | \ f_i,\theta), \nonumber \\
    \mathbf{f} \ | \ \theta &\sim& \mathcal{GP}\left(m_{\theta}(\mathbf{x}), k_{\theta}(\mathbf{x}, \mathbf{x}')\right),\\
      \theta &\sim& p(\theta), \nonumber
\end{eqnarray}
where $\mathbf{y}=(y_1,y_2,\ldots,y_n) \in \mathcal{Y}$ and $\mathbf{x} \in \mathcal{X}$ are the observations and covariates, respectively, and $f_i:=f(\mathbf{x}_i)$ is the latent function which we model with a Gaussian process prior. We assume that the responses $\mathbf{y}$ are independent and identically distributed and as a result the likelihood $p(\mathbf{y} \ | \ \mathbf{f}, \theta)$, can be factorized over the observations. 

In the case where the observations are Gaussian distributed, the marginal likelihood and predictive distribution can be derived analytically. See the  [Regression notebook](https://github.com/STOR-i/GaussianProcesses.jl/blob/master/notebooks/Regression.ipynb) for an illustration.

In this example we show how the GP **Monte Carlo** function can be used for **supervised learning classification**. We use the Crab dataset from the R package MASS. In this dataset we are interested in predicting whether a crab is of colour form blue or orange. Our aim is to perform a Bayesian analysis and calculate the posterior distribution of the latent GP function $\mathbf{f}$ and model parameters $\theta$ from the training data $\{\mathbf{X}, \mathbf{y}\}$.

In [9]:
using GaussianProcesses, RDatasets

srand(113355)

crabs = dataset("MASS","crabs");              # load the data 
crabs = crabs[shuffle(1:size(crabs)[1]), :];  # shuffle the data

train = crabs[1:div(end,2),:];

y = Array(Bool,size(train)[1]);           # response
y[train[:Sp].=="B"]=0;                      # convert characters to booleans
y[train[:Sp].=="O"]=1;

X = convert(Array,train[:,4:end]);          # predictors

We assume a zero mean GP with a Matern 3/2 kernel. We use the automatic relevance determination (ARD) kernel to allow each dimension of the predictor variables to have a different length scale. As this is binary classifcation, we use the Bernoulli likelihood, 

$$
y_i \sim Bernoulli(\Phi(f_i))
$$
where $\Phi: \mathbb{R} \rightarrow [0,1]$ is the cumulative distribution function of a standard Gaussian and acts as a squash function that maps the GP function to the interval [0,1], giving the probability that $y_i=1$. 

**Note** that `BernLik` requires the observations to be of type `Bool` and unlike some likelihood functions (e.g. student-t) does not contain any parameters to be set at initialisation.

In [10]:
#Select mean, kernel and likelihood function
mZero = MeanZero();                # Zero mean function
kern = Matern(3/2,zeros(5),0.0);   # Matern 3/2 ARD kernel (note that hyperparameters are on the log scale)
lik = BernLik();                   # Bernoulli likelihood for binary data {0,1}

We fit the GP using the general `GP` function. This function is a shorthand for the `GPMC` function which is used to generate **Monte Carlo approximations** of the latent function when the **likelihood is non-Gaussian**. 

In [11]:
gp = GP(X',y,mZero,kern,lik)      # Fit the Gaussian process model

GP Monte Carlo object:
  Dim = 5
  Number of observations = 100
  Mean function:
    Type: GaussianProcesses.MeanZero, Params: Float64[]
  Kernel:
    Type: GaussianProcesses.Mat32Ard, Params: [-0.0,-0.0,-0.0,-0.0,-0.0,0.0]
  Likelihood:
    Type: GaussianProcesses.BernLik, Params: Any[]
  Input observations = 
[16.2 11.2 … 11.6 18.5; 13.3 10.0 … 9.1 14.6; … ; 41.7 26.9 … 28.4 42.0; 15.4 9.4 … 10.4 16.6]
  Output observations = Bool[false,false,false,false,true,true,false,true,true,true  …  false,true,false,false,false,true,false,false,false,true]
  Log-posterior = -161.209

We assign `Normal` priors from the `Distributions` package to each of the Matern kernel parameters. If the mean and likelihood function also contained parameters, then we could set these priors in the same using `gp.m` and `gp.lik` in place of `gp.k`, respectively.

In [12]:
set_priors!(gp.k,[Distributions.Normal(0.0,2.0) for i in 1:6])

6-element Array{Distributions.Normal{Float64},1}:
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)
 Distributions.Normal{Float64}(μ=0.0, σ=2.0)

Samples of the latent function $f | X,y,\theta$ are drawn using MCMC sampling. The MCMC routine uses the `Klara` package. By default, the `mcmc` function uses the MALA algorithm, where the stepsize is automatically tuned to a desired acceptance rate. Alternative samplers, such as HMC and NUTS, can also be used. 

In [13]:
samples = mcmc(gp)

BasicMCJob:
  Variable [1]: p (Klara.BasicContMuvParameter)
  GenericModel: 1 variables, 0 dependencies (directed graph)
  MALA sampler: drift step = 0.1
  VanillaMCTuner: period = 100, verbose = false
  BasicMCRange: number of steps = 5000, burnin = 1000, thinning = 1
  plain = true (job flow not controlled by tasks)

106×4000 Array{Float64,2}:
 -0.300791   -0.300791   -0.300791   …  -0.502692   -0.502692   -0.502692 
 -1.1035     -1.1035     -1.1035        -0.996795   -0.996795   -0.996795 
 -0.768605   -0.768605   -0.768605      -0.374754   -0.374754   -0.374754 
 -0.831663   -0.831663   -0.831663      -0.03474    -0.03474    -0.03474  
  1.53533     1.53533     1.53533        1.38691     1.38691     1.38691  
  0.87194     0.87194     0.87194    …   2.39914     2.39914     2.39914  
 -1.12568    -1.12568    -1.12568       -1.27901    -1.27901    -1.27901  
  0.486501    0.486501    0.486501       0.47746     0.47746     0.47746  
  1.0202      1.0202      1.0202         1.1653      1.1653      1.1653   
  0.757028    0.757028    0.757028      -0.0486324  -0.0486324  -0.0486324
  0.116483    0.116483    0.116483   …   0.533791    0.533791    0.533791 
 -1.07913    -1.07913    -1.07913       -1.69142    -1.69142    -1.69142  
 -0.717561   -0.717561   -0.717561      -1.16222    -1.16222    -1.16222 

We test the predictive accuracy of the fitted model against a hold-out dataset

In [14]:
test = crabs[div(end,2)+1:end,:];   # select test data

yTest = Array(Bool,size(test)[1]);        # test response data
yTest[test[:Sp].=="B"]=0;                      # convert characters to booleans
yTest[test[:Sp].=="O"]=1;

xTest = convert(Array,test[:,4:end]);

Using the posterior samples $\{f^{(i)},\theta^{(i)}\}_{i=1}^N$ from $p(f,\theta \ | \ X,y)$ we can make predictions $\hat{y}$ using the `predict_y` function to sample predictions conditional on the MCMC samples.

In [15]:
ymean = Array(Float64,size(samples,2),size(xTest,1));

for i in 1:size(samples,2)
    set_params!(gp,samples[:,i])
    update_target!(gp)
    ymean[i,:] = predict_y(gp,xTest')[1]
end

For each of the posterior samples we plot the predicted observation $\hat{y}$ (given as lines) and overlay the true observations from the held-out data (circles).

In [16]:
using Plots
gr()

plot(ymean',leg=false)
scatter!(yTest)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0 
 
 
 50 
 
 
 100 
 
 
 0.0 
 
 
 0.5 
 
 
 1.0 
 
<polyline clip-path="url(#clip02)" style="stroke:#009af9; stroke-width:1; stroke-opacity:1; fill:none" points="
 55.0141,131.395 60.2815,18.0903 65.5488,18.0805 70.8162,133.629 76.0835,358.297 81.3509,358.297 86.6182,113.265 91.8856,85.5063 97.1529,33.5312 102.42,358.296 
 107.688,203.413 112.955,358.297 118.222,19.2135 123.49,358.297 128.757,19.5725 134.024,356.365 139.292,18.5863 144.559,18.0814 149.826,216.585 155.094,18.0812 
 160.361,18.0812 165.629,60.7206 170.896,158.287 176.163,357.5 181.431,335.91 186.698,101.093 191.965,333.39 197.233,352.144 202.5,18.0805 207.767,357.024 
 213.035,342.164 218.302,18.0805 223.569,358.297 228.837,25.8505 234.104,21.5059 239.371,357.362 244.639,332.173 249.906,355.8 255.173,31.6693 260.441,350.716 
 265.708,358.297 270.976,44.7332 276.243,18.0805 281.51,153.043 286.778,29.058 292.045,358.297 297.312,18.0805 302.58,358.297 307.847,358.003 313.114,358.295 
 318.382,357.215 323.649,19.0155 328.916,18.9243 334.184,358.296 339.451,34.142 344.718,243.568 349.986,358.112 355.253,18.5912 360.521,313.568 365.788,358.297 
 371.055,323.084 376.323,18.4756 381.59,117.52 386.857,30.2921 392.125,139.163 397.392,354.41 402.659,18.0868 407.927,120.47 413.194,355.958 418.461,358.283 
 423.729,82.8207 428.996,173.887 434.263,354.475 439.531,18.0805 444.798,352.379 450.066,357.685 455.333,358.297 460.6,34.5532 465.868,32.8716 471.135,195.793 
 476.402,20.1967 481.67,184.34 486.937,307.263 492.204,18.0805 497.472,289.494 502.739,241.447 508.006,20.3822 513.274,18.8172 518.541,18.0806 523.808,70.9291 
 529.076,25.9452 534.343,350.796 539.61,27.2192 544.878,104.342 550.145,22.7321 555.413,358.297 560.68,357.721 565.947,18.0805 571.215,357.989 576.482,67.3404 
 
 "/>
<polyline clip-path="url(#clip02)" style="stroke:#e26f46; stroke-width:1; stroke-opacity:1; fill:none" points="
 55.0141,131.395 60.2815,18.0903 65.5488,18.0805 70.8162,133.629 76.0835,358.297 81.3509,358.297 86.6182,113.265 91.8856,85.5063 97.1529,33.5312 102.42,358.296 
 107.688,203.413 112.955,358.297 118.222,19.2135 123.49,358.297 128.757,19.5725 134.024,356.365 139.292,18.5863 144.559,18.0814 149.826,216.585 155.094,18.0812 
 160.361,18.0812 165.629,60.7206 170.896,158.287 176.163,357.5 181.431,335.91 186.698,101.093 191.965,333.39 197.233,352.144 202.5,18.0805 207.767,357.024 
 213.035,342.164 218.302,18.0805 223.569,358.297 228.837,25.8505 234.104,21.5059 239.371,357.362 244.639,332.173 249.906,355.8 255.173,31.6693 260.441,350.716 
 265.708,358.297 270.976,44.7332 276.243,18.0805 281.51,153.043 286.778,29.058 292.045,358.297 297.312,18.0805 302.58,358.297 307.847,358.003 313.114,358.295 
 318.382,357.215 323.649,19.0155 328.916,18.9243 334.184,358.296 339.451,34.142 344.718,243.568 349.986,358.112 355.253,18.5912 360.521,313.568 365.788,358.297 
 371.055,323.084 376.323,18.4756 381.59,117.52 386.857,30.2921 392.125,139.163 397.392,354.41 402.659,18.0868 407.927,120.47 413.194,355.958 418.461,358.283 
 423.729,82.8207 428.996,173.887 434.263,354.475 439.531,18.0805 444.798,352.379 450.066,357.685 455.333,358.297 460.6,34.5532 465.868,32.8716 471.135,195.793 
 476.402,20.1967 481.67,184.34 486.937,307.263 492.204,18.0805 497.472,289.494 502.739,241.447 508.006,20.3822 513.274,18.8172 518.541,18.0806 523.808,70.9291 
 529.076,25.9452 534.343,350.796 539.61,27.2192 544.878,104.342 550.145,22.7321 555.413,358.297 560.68,357.721 565.947,18.0805 571.215,357.989 576.482,67.3404 
 
 "/>
<polyline clip-path="url(#clip02)" style="stroke:#3da44d; stroke-width:1; stroke-opacity:1; fill:none" points="
 55.0141,131.395 60.2815,18.0903 65.5488,18.0805 70.8162,133.629 76.0835,358.297 81.3509,358.297 86.6182,113.265 91.8856,85.5063 97.1529,33.5312 102.42,358.296 
 107.688,203.413 112.955,358.297 118.222,19.2135 123.49,358.297 128.757,19.5725 134.024,356.365 139.292,18.5863 144.559,18.0814 149.826,2